#### INFO
implementirani so okolje, prey, predator, rewards in decision logic, trace, observation 6 sosedov, animacija

niso vsi parametri kt so velikost zemljevida in hitrost enaki kt v articlu, ampak mislm da to nima veze. se pa lahko poprav.

passive in active forces se mi zdijo mau problematični. mi ni ratal implementirat. (v clanku opisan pod agent dynamics). ker aF in aR nist aimplementirala, tut decorative reward za laziness (−0.01|aF| − 0.1|aR) ni implementiran.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML
import torch
import torch.nn as nn
import torch.optim as optim
from matplotlib.lines import Line2D
import random

In [2]:
class ReplayBuffer:
    def __init__(self, capacity=10000):
        self.buffer = []
        self.capacity = capacity

    def add(self, experience):
        if len(self.buffer) >= self.capacity:
            self.buffer.pop(0)
        self.buffer.append(experience)

    def sample(self, batch_size):
        return random.sample(self.buffer, batch_size)

In [3]:
class ActorNetwork(nn.Module):
    def __init__(self, input_dim, output_dim):
        super(ActorNetwork, self).__init__()
        self.fc1 = nn.Linear(input_dim, 128)
        self.fc2 = nn.Linear(128, 128)
        self.fc3 = nn.Linear(128, output_dim)

    def forward(self, x):
        x = torch.relu(self.fc1(x))
        x = torch.relu(self.fc2(x))
        x = torch.tanh(self.fc3(x))  # Actions are continuous, scaled between -1 and 1
        return x

In [4]:
class CriticNetwork(nn.Module):
    def __init__(self, input_dim):
        super(CriticNetwork, self).__init__()
        self.fc1 = nn.Linear(input_dim, 128)
        self.fc2 = nn.Linear(128, 128)
        self.fc3 = nn.Linear(128, 1)

    def forward(self, x):
        x = torch.relu(self.fc1(x))
        x = torch.relu(self.fc2(x))
        x = self.fc3(x)
        return x

In [33]:
class Agent:
    def __init__(self, position, speed, mass, max_acceleration, max_angular_velocity, agent_type):
        self.position = np.array(position, dtype=float)
        self.velocity = np.random.uniform(-1, 1, 2)
        if np.linalg.norm(self.velocity) == 0:
            self.velocity = np.array([1.0, 0.0])
        else:
            self.velocity = (self.velocity / np.linalg.norm(self.velocity)) * speed
        self.mass = mass
        self.type = agent_type
        self.heading_angle = np.arctan2(self.velocity[1], self.velocity[0])
        self.heading_vector = np.array([np.cos(self.heading_angle), np.sin(self.heading_angle)])
        self.acceleration = np.zeros(2)

        self.max_acceleration = max_acceleration
        self.max_angular_velocity = max_angular_velocity
        self.position_history = [self.position.copy()]

        self.drag_coefficient = 0.1  # reduced 

        self.stiffness_coefficient = 100.0  # increased 
        self.collision_force = np.zeros(2)
        self.radius = 2.0 if agent_type == 'predator' else 1.0  # agent size

    def move(self, dt=0.3):  # made dt to 0.3
        pass

    def apply_boundary_conditions(self, width, height):
        self.position = self.position % np.array([width, height])


In [38]:
class Prey(Agent):
    def __init__(self, position, **kwargs):
        super().__init__(position, speed=2.0, mass=1.0, max_acceleration=5.0, max_angular_velocity=2.0, agent_type='prey')
        self.is_captured = False

    def move(self, dt=0.3):
        # Active forces
        nearest_predator = env.find_nearest_predator(self, perception_range=30.0)
        if nearest_predator is not None:
            # Compute direction away from predator
            direction_away = self.position - nearest_predator.position
            direction_away = env.apply_periodic_adjustment(direction_away)
            distance = np.linalg.norm(direction_away)
            if distance > 0:
                desired_heading = direction_away / distance
            else:
                desired_heading = self.heading_vector
            # Update heading away from predator with angular speed limit
            angle_diff = np.arctan2(desired_heading[1], desired_heading[0]) - self.heading_angle
            angle_diff = (angle_diff + np.pi) % (2 * np.pi) - np.pi
            max_turn = self.max_angular_velocity * dt
            if abs(angle_diff) > max_turn:
                angle_diff = np.sign(angle_diff) * max_turn
            self.heading_angle += angle_diff
            self.heading_vector = np.array([np.cos(self.heading_angle), np.sin(self.heading_angle)])
        else:
            # Slight random walk if no predator nearby
            random_turn = np.random.uniform(-self.max_angular_velocity, self.max_angular_velocity) * dt * 0.1
            self.heading_angle += random_turn
            self.heading_vector = np.array([np.cos(self.heading_angle), np.sin(self.heading_angle)])

        # Record the rotational acceleration (control effort)
        a_R = angle_diff / dt if nearest_predator is not None else random_turn / dt

        a_F = self.max_acceleration  # Use max acceleration

        # Propulsion force
        propulsion_force = a_F * self.heading_vector

        # Passive forces
        drag_force = -self.drag_coefficient * self.velocity
        collision_force = self.collision_force

        # Total force
        total_force = propulsion_force + drag_force + collision_force

        # Update velocity
        prev_velocity = self.velocity.copy()
        self.velocity += (total_force / self.mass) * dt

        # Compute the forward acceleration (control effort)
        a_F_actual = (np.linalg.norm(self.velocity) - np.linalg.norm(prev_velocity)) / dt

        # Limit speed
        speed_limit = 5.0
        speed = np.linalg.norm(self.velocity)
        if speed > speed_limit:
            self.velocity = (self.velocity / speed) * speed_limit

        # Update position
        self.position += self.velocity * dt

        # Apply boundary conditions
        self.apply_boundary_conditions(env.width, env.height)

        # Reset collision force
        self.collision_force = np.zeros(2)

        # Update position history
        self.position_history.append(self.position.copy())
        if len(self.position_history) > 10:
            self.position_history.pop(0)

        # --- Reward System Implementation ---

        # Check if captured by any predator
        self.is_captured = False
        for agent in env.agents:
            if agent.type == 'predator':
                distance_vector = self.position - agent.position
                distance_vector = env.apply_periodic_adjustment(distance_vector)
                distance = np.linalg.norm(distance_vector)
                if distance < (self.radius + agent.radius):
                    self.is_captured = True
                    break

        # Calculate reward
        if self.is_captured:
            reward = -100.0  # Penalty for being caught
        else:
            reward = 1.0  # Survival reward

        # Movement cost penalties
        reward -= 0.1 * abs(a_F_actual)  # Penalty for acceleration
        reward -= 0.1 * abs(a_R)         # Penalty for rotation

        # Get observation
        observation = self.get_observation()

        # Store experience in replay buffer
        state = observation
        action = np.array([a_F_actual, a_R])  # Control actions
        next_state = self.get_observation()

        env.replay_buffer_prey.add((state, action, reward, next_state))


In [39]:
class Predator(Agent):
    def __init__(self, position, **kwargs):
        super().__init__(position, speed=2.5, mass=1.0, max_acceleration=6.0, max_angular_velocity=2.5, agent_type='predator')

    def move(self, dt=0.3):
        # Active forces
        nearest_prey = env.find_nearest_prey(self)
        if nearest_prey is not None:
            # Compute direction towards prey
            direction_to_prey = nearest_prey.position - self.position
            direction_to_prey = env.apply_periodic_adjustment(direction_to_prey)
            distance = np.linalg.norm(direction_to_prey)
            if distance > 0:
                desired_heading = direction_to_prey / distance
            else:
                desired_heading = self.heading_vector
            # Update heading towards prey with angular speed limit
            angle_diff = np.arctan2(desired_heading[1], desired_heading[0]) - self.heading_angle
            angle_diff = (angle_diff + np.pi) % (2 * np.pi) - np.pi
            max_turn = self.max_angular_velocity * dt
            if abs(angle_diff) > max_turn:
                angle_diff = np.sign(angle_diff) * max_turn
            self.heading_angle += angle_diff
            self.heading_vector = np.array([np.cos(self.heading_angle), np.sin(self.heading_angle)])
        else:
            # Random walk if no prey detected
            random_turn = np.random.uniform(-self.max_angular_velocity, self.max_angular_velocity) * dt * 0.1
            self.heading_angle += random_turn
            self.heading_vector = np.array([np.cos(self.heading_angle), np.sin(self.heading_angle)])

        # Record the rotational acceleration (control effort)
        a_R = angle_diff / dt if nearest_prey is not None else random_turn / dt

        a_F = self.max_acceleration  # Use max acceleration

        # Propulsion force
        propulsion_force = a_F * self.heading_vector

        # Passive forces
        drag_force = -self.drag_coefficient * self.velocity
        collision_force = self.collision_force

        # Total force
        total_force = propulsion_force + drag_force + collision_force

        # Update velocity
        prev_velocity = self.velocity.copy()
        self.velocity += (total_force / self.mass) * dt

        # Compute the forward acceleration (control effort)
        a_F_actual = (np.linalg.norm(self.velocity) - np.linalg.norm(prev_velocity)) / dt

        # Limit speed
        speed_limit = 6.0
        speed = np.linalg.norm(self.velocity)
        if speed > speed_limit:
            self.velocity = (self.velocity / speed) * speed_limit

        # Update position
        self.position += self.velocity * dt

        # Apply boundary conditions
        self.apply_boundary_conditions(env.width, env.height)

        # Reset collision force
        self.collision_force = np.zeros(2)

        # Update position history
        self.position_history.append(self.position.copy())
        if len(self.position_history) > 10:
            self.position_history.pop(0)

        # --- Reward System Implementation ---

        # Check if any prey is captured
        captured_prey = None
        for agent in env.agents:
            if agent.type == 'prey':
                distance_vector = self.position - agent.position
                distance_vector = env.apply_periodic_adjustment(distance_vector)
                distance = np.linalg.norm(distance_vector)
                if distance < (self.radius + agent.radius):
                    captured_prey = agent
                    break

        # Calculate reward
        if captured_prey:
            reward = 100.0  # Reward for capturing prey
            env.agents.remove(captured_prey)  # Remove captured prey from environment
        else:
            reward = -1.0  # Small penalty for not capturing prey

        # Movement cost penalties
        reward -= 0.1 * abs(a_F_actual)  # Penalty for acceleration
        reward -= 0.1 * abs(a_R)         # Penalty for rotation

        # Get observation
        observation = self.get_observation()

        # Store experience in replay buffer
        state = observation
        action = np.array([a_F_actual, a_R])  # Control actions
        next_state = self.get_observation()

        env.replay_buffer_predator.add((state, action, reward, next_state))


In [40]:
class PredatorPreyEnvironment:
    def __init__(self, width=100, height=100):
        self.width = width
        self.height = height
        self.agents = []
        self.stiffness_coefficient = 100.0  # Increased for stronger collision response

        # Initialize replay buffers
        self.replay_buffer_prey = ReplayBuffer(capacity=10000)
        self.replay_buffer_predator = ReplayBuffer(capacity=10000)


    def add_agent(self, agent):
        self.agents.append(agent)

    def update(self, dt=0.3):  # Adjusted dt to 0.3
        # Compute collision forces
        self.compute_collision_forces()

        # Update each agent
        for agent in self.agents:
            agent.move(dt=dt)

    def compute_collision_forces(self):
        # Initialize collision forces for all agents
        for agent in self.agents:
            agent.collision_force = np.zeros(2)

        num_agents = len(self.agents)
        for i in range(num_agents):
            agent_i = self.agents[i]
            for j in range(i + 1, num_agents):
                agent_j = self.agents[j]
                distance_vector = agent_i.position - agent_j.position
                # Adjust for periodic boundaries
                distance_vector = self.apply_periodic_adjustment(distance_vector)
                distance = np.linalg.norm(distance_vector)
                min_distance = agent_i.radius + agent_j.radius
                if distance < min_distance and distance > 0:
                    # Compute elastic force
                    overlap = min_distance - distance
                    direction = distance_vector / distance
                    force_magnitude = self.stiffness_coefficient * overlap
                    force = force_magnitude * direction
                    agent_i.collision_force += force
                    agent_j.collision_force -= force  # Equal and opposite force

    def apply_periodic_adjustment(self, vector):
        # Adjust vector components for periodic boundary conditions
        adjusted_vector = vector.copy()
        if vector[0] > self.width / 2:
            adjusted_vector[0] -= self.width
        elif vector[0] < -self.width / 2:
            adjusted_vector[0] += self.width
        if vector[1] > self.height / 2:
            adjusted_vector[1] -= self.height
        elif vector[1] < -self.height / 2:
            adjusted_vector[1] += self.height
        return adjusted_vector

    def find_nearest_prey(self, predator):
        nearest_prey = None
        min_distance = float('inf')
        for agent in self.agents:
            if agent.type == 'prey':
                distance_vector = agent.position - predator.position
                distance_vector = self.apply_periodic_adjustment(distance_vector)
                distance = np.linalg.norm(distance_vector)
                if distance < min_distance:
                    min_distance = distance
                    nearest_prey = agent
        return nearest_prey

    def find_nearest_predator(self, prey, perception_range=30.0):
        nearest_predator = None
        min_distance = float('inf')
        for agent in self.agents:
            if agent.type == 'predator':
                distance_vector = agent.position - prey.position
                distance_vector = self.apply_periodic_adjustment(distance_vector)
                distance = np.linalg.norm(distance_vector)
                if distance < min_distance and distance <= perception_range:
                    min_distance = distance
                    nearest_predator = agent
        return nearest_predator

    def adjust_positions_for_traces(self, positions):
        """
        Adjust positions to account for toroidal boundaries in traces.
        This prevents lines from being drawn across the plot when agents wrap around.
        """
        adjusted_positions = [positions[0]]
        for i in range(1, len(positions)):
            prev = adjusted_positions[-1]
            curr = positions[i].copy()
            dx = curr[0] - prev[0]
            dy = curr[1] - prev[1]

            # Adjust for wrapping in x-direction
            if dx > self.width / 2:
                curr[0] -= self.width
            elif dx < -self.width / 2:
                curr[0] += self.width

            # Adjust for wrapping in y-direction
            if dy > self.height / 2:
                curr[1] -= self.height
            elif dy < -self.height / 2:
                curr[1] += self.height

            adjusted_positions.append(curr)
        return np.array(adjusted_positions)

    def get_agent_shape(self, agent):
        """
        Return the vertices of a triangle representing the agent's orientation.
        """
        direction = agent.heading_vector
        direction = direction / np.linalg.norm(direction)
        perp_direction = np.array([-direction[1], direction[0]])
        size = agent.radius * 2  # Scale the size based on agent's radius
        front = agent.position + direction * size  # Length of the triangle
        left = agent.position - direction * size * 0.5 + perp_direction * size * 0.5  # Triangle base left
        right = agent.position - direction * size * 0.5 - perp_direction * size * 0.5  # Triangle base right
        return [front, left, right]

    def animate(self, steps=100):
        """
        Animate the simulation.
        """
        fig, ax = plt.subplots(figsize=(5, 5))
        ax.set_xlim(0, self.width)
        ax.set_ylim(0, self.height)
        ax.set_xticks([])
        ax.set_yticks([])

        # Initialize a dictionary to keep track of agent patches and traces
        agent_artists = {}

        # Initialize the agents' patches and traces
        for agent in self.agents:
            if agent.type == 'prey':
                triangle = plt.Polygon(self.get_agent_shape(agent), closed=True, color='b')
                line, = ax.plot([], [], color='b', alpha=0.2)
            elif agent.type == 'predator':
                triangle = plt.Polygon(self.get_agent_shape(agent), closed=True, color='orange', alpha=0.8)
                line, = ax.plot([], [], color='orange', alpha=0.2)
            agent_artists[agent] = {'patch': triangle, 'trace': line}
            ax.add_patch(triangle)

        def update(frame):
            self.update(dt=0.3)

            # Update positions and traces
            for agent in self.agents:
                artist = agent_artists[agent]
                patch = artist['patch']
                trace = artist['trace']

                patch.set_xy(self.get_agent_shape(agent))
                # Update the trace with the agent's position history
                positions = np.array(agent.position_history)
                # Adjust positions for toroidal wrapping
                positions = self.adjust_positions_for_traces(positions)
                trace.set_data(positions[:, 0], positions[:, 1])

            return []

        ani = animation.FuncAnimation(fig, update, frames=steps, blit=False, interval=50, repeat=False)
        plt.close(fig)  # Close the figure to prevent additional static display
        return HTML(ani.to_jshtml())


In [ ]:
# Create environment instance
width = 70
env = PredatorPreyEnvironment(width, width)

# Add prey agents
num_prey = 15
for _ in range(num_prey):
    initial_position = np.random.uniform(0, width, 2)
    prey = Prey(position=initial_position)
    env.add_agent(prey)

# Add predator agents
num_predators = 5
for _ in range(num_predators):
    initial_position = np.random.uniform(0, width, 2)
    predator = Predator(position=initial_position)
    env.add_agent(predator)

# Animate the environment
animation_html = env.animate(steps=200)
animation_html
